In [1]:
import netgen.gui
# ngsolve stuff
from ngsolve import *
# basic geometry features (for the background mesh)
from netgen.geom2d import SplineGeometry
# visualization stuff
from ngsolve.internal import *
# basic xfem functionality
from xfem import *

box = SplineGeometry()
pnts = [(0, 0), (1, 0), (1, 1), (0, 1)]
pind = [ box.AppendPoint(*pnt) for pnt in pnts ]
box.Append(['line',pind[0],pind[1]],leftdomain=1,rightdomain=0,bc="bottom")
box.Append(['line',pind[1],pind[2]],leftdomain=1,rightdomain=0,bc="right")
box.Append(['line',pind[2],pind[3]],leftdomain=1,rightdomain=0,bc="top")
box.Append(['line',pind[3],pind[0]],leftdomain=1,rightdomain=0,bc="left")

mesh = Mesh (box.GenerateMesh(maxh=0.25, quad_dominated=False))

In [2]:
V1 = H1(mesh, order=1)
V2=H1(mesh, order=1, dim=mesh.dim)


ls = GridFunction(V1)
lsd = (sqrt(5*x**2+10*(y-0.5)**2) - 1.0)



E = 1
nu = 0.3
mu = E/(2*(1+nu))
lam = nu*E/((1-2*nu)*(1+nu))
kappa = (lam+3*mu)/(lam + mu)
alpha_in = 1
alpha_out = 0.001
r_out = alpha_in/alpha_out
r_in=1/r_out
I=Id(2)
tol=0.0001



gforce = GridFunction(V2)

for v in mesh.vertices:
    if abs(v.point[0]-1) + (max(abs(v.point[1]-0.5),0.01)-0.01) < tol:
        for dof in V2.GetDofNrs(v):
            gforce.vec[dof][1]=-1.0


In [3]:
InterpolateToP1(lsd,ls)
Draw(ls,mesh,"ls")
ci = CutInfo(mesh, ls)

# extended FESpace 
Vh = H1(mesh, order=1, dim=mesh.dim, dirichlet="left")
Vhx = XFESpace(Vh,ci)
VhG = FESpace([Vh,Vhx])

VhGx, VhGy = VhG.components
freedofs = VhG.FreeDofs()
print(freedofs)

for el in mesh.Elements(BND):
    for v in el.vertices:
        w=mesh[v]
        if abs(w.point[0])<tol:
            for dof in VhG.GetDofNrs(w):
                freedofs.Clear(dof)
                freedofs.Clear(VhGx.ndof+dof)
print(freedofs)                  

# coefficients / parameters:
n = 1.0/grad(ls).Norm() * grad(ls)
h = specialcf.mesh_size

# the cut ratio extracted from the cutinfo-class
cutRatio = (CutRatioGF(ci),1.0-CutRatioGF(ci))

# Nitsche stabilization parameter:
stab = 20*(alpha_in+alpha_out)/h

# expressions of test and trial functions:
u_std, u_x = VhG.TrialFunction()
v_std, v_x = VhG.TestFunction()

u = [u_std + op(u_x) for op in [neg,pos]]
v = [v_std + op(v_x) for op in [neg,pos]]

gradu = [grad(u_std) + op(u_x) for op in [neg_grad,pos_grad]]
gradv = [grad(v_std) + op(v_x) for op in [neg_grad,pos_grad]]

gradu_trans = [gt.trans for gt in gradu]
gradv_trans = [gt.trans for gt in gradv]


epsu = [0.5*(gradu[i]+gradu_trans[i]) for i in [0,1]]
epsv = [0.5*(gradv[i]+gradv_trans[i]) for i in [0,1]]

sigmau = [2*mu*epsu[i]+lam*Trace(epsu[i])*I for i in [0,1]]
sigmav = [2*mu*epsv[i]+lam*Trace(epsv[i])*I for i in [0,1]]

average_flux_u = - cutRatio[0] * alpha_in * sigmau[0] * n - cutRatio[1] * alpha_out * sigmau[1] * n
average_flux_v = - cutRatio[0] * alpha_in * sigmav[0] * n - cutRatio[1] * alpha_out * sigmav[1] * n 

# Integration domains for integration on negative/positive subdomains and on the interface:
# Here, the integration is (geometrically) exact if the "levelset"-argument is a piecewise
# (multi-)linear function. The integration order is chosen according to the arguments in the
# multilinear forms (but can be overwritten with "force_intorder" in the integration domain). If the
# "levelset"-argument is not a (multi-)linear function, you can use the "subdivlvl" argument to add
# additional refinement levels for the geometry approximation. 
lset_neg = { "levelset" : CoefficientFunction(ls+0), "domain_type" : NEG, "subdivlvl" : 0}
lset_pos = { "levelset" : CoefficientFunction(ls+0), "domain_type" : POS, "subdivlvl" : 0}
lset_if  = { "levelset" : CoefficientFunction(ls+0), "domain_type" : IF , "subdivlvl" : 0}

# bilinear forms:
a = BilinearForm(VhG, symmetric = True)
# l.h.s. domain integrals:
a += SymbolicBFI(levelset_domain = lset_neg, form = alpha_in * InnerProduct(sigmau[0],epsv[0]))
a += SymbolicBFI(levelset_domain = lset_pos, form = alpha_out * InnerProduct(sigmau[1],epsv[1]))
# Nitsche integrals:
a += SymbolicBFI(levelset_domain = lset_if , form =       InnerProduct(average_flux_u,(v[0]-v[1]))
                                                    +     InnerProduct(average_flux_v,(u[0]-u[1]))
                                                    + stab * InnerProduct((u[0]-u[1]),(v[0]-v[1])))

fu = LinearForm(VhG)
# r.h.s. domain integrals:
fu += SymbolicLFI(form=InnerProduct(gforce,v), VOL_or_BND=BND)

# solution vector
gfu = GridFunction(VhG)

# setting up matrix and vector
a.Assemble();
fu.Assemble();
# homogenization of boundary data and solution of linear system
gfu.vec.data = a.mat.Inverse(freedofs=VhG.FreeDofs()) * fu.vec

u_coef = gfu.components[0] + IfPos(ls, pos(gfu.components[1]), neg(gfu.components[1]))
u_xfem = IfPos(ls, pos(gfu.components[1]), neg(gfu.components[1]))

0: 0110111111111000111111111111111111111
0: 0110111111111000111111111110010011111


NgException: Testfunction does not support BND-forms, maybe a Trace() operator is missing